In [1]:
import pandas as pd
import numpy as np
import geopandas as gpd
import os
import glob
import json
import re

In [2]:
data_folder = r'D:\CivicDataLab_IDS-DRR\IDS-DRR_Github\IDS-DRR-Assam\Sources\FRIMS\data\DRIMS_api_output'

In [3]:
data = open(r'D:\CivicDataLab_IDS-DRR\IDS-DRR_Github\IDS-DRR-Assam\Sources\FRIMS\data\DRIMS_api_output\2024_07.json')
data_file = json.load(data)
data_file

{'cwcDetails': {'riversAtWarningLevel': 'Brahmaputra (Dibrugarh), Brahmaputra (Guwahati), Brahmaputra (Dhubri), Ranganadi (Nt Road Crossing), Dhansiri (S) (Numaligarh), Puthimari (Nh Road Crossing), Pagladiya (Nt Road Crossing), Gaurang (Kokrajhar), Sankosh (Golokganj), Brahmaputra (Goalpara), Burhidihing (Naharkatia), Kopili (Dharamtul), Jia-Bharali (Nt Road Crossing), Dhansiri (S) (Golaghat), Beki (Road Bridge), Subansiri (Badatighat), Brahmaputra (Tezpur), Kopili (Kampur), Dikhou (Sivasagar), Burhidihing (Chenimari(Khowang)), Brahmaputra (Neamatighat), Disang (Nanglamuraghat)',
  'riversAtDangerLevel': 'Brahmaputra (Tezpur), Subansiri (Badatighat), Dikhou (Sivasagar), Disang (Nanglamuraghat), Burhidihing (Chenimari(Khowang)), Jia-Bharali (Nt Road Crossing), Beki (Road Bridge), Brahmaputra (Neamatighat), Brahmaputra (Guwahati), Brahmaputra (Dhubri), Dhansiri (S) (Numaligarh), Puthimari (Nh Road Crossing), Kopili (Kampur), Brahmaputra (Goalpara), Kopili (Dharamtul), Sankosh (Golokganj

In [3]:
def extract_damage_names(data, damage_names=None):
    if damage_names is None:
        damage_names = set()

    # Check if 'damageName' exists at the current level
    if isinstance(data, dict):
        if 'damageName' in data:
            damage_names.add(data['damageName'])
        
        # Recursively go deeper into the dictionary
        for key, value in data.items():
            extract_damage_names(value, damage_names)
    
    elif isinstance(data, list):
        # If the data is a list, iterate over its elements
        for item in data:
            extract_damage_names(item, damage_names)
    
    return damage_names

damage_names = extract_damage_names(data_file)

# Count the number of unique damageName entries
unique_damage_names_count = len(damage_names)

print("Unique 'damageName' entries:", damage_names)
print("Count of unique 'damageName' entries:", unique_damage_names_count)


Unique 'damageName' entries: {'Agri Bundh Damaged (in Nos)', 'Fisheries/Pond (in Nos)', 'Veterinary Deptt Infrastructure (in Nos)', 'Bamboo Foot Bridge (in Nos)', 'Irrigation Canal/Scheme Damaged (in Nos)', 'Power Dept. Transformers (in Nos)', 'Bridge Approach Road Washed Away (in Nos)', 'Health Sub-Centre (in Nos)', 'Sericulture Deptt. Damaged (in Nos)', 'Anganwadi Centres Affected (in Nos)', 'Raised Plateform Damaged (in Nos)', 'Damaged SPT Bridge (in Nos)', 'Washed away SPT Bridge (in Nos)', 'Culvert Approach Road Damaged (in Nos)', 'Road Breaches (in Nos)', 'Bridge Approach Road Damaged (in Nos)', 'Damaged RCC Bridge (in Nos)', 'Power Dept. Poles (in Nos)', 'Protection Bundh Damaged (in Nos)', 'Handloom & Textile Deptt (in Nos)', 'Gully Control Damaged (in Nos)', 'Inland Water Transport Deptt. Damaged (in Nos)', 'Elementary Schools Damaged (in Nos)', 'Washed away Culverts (in Nos)', 'Power Dept. Conductors (in Nos)', 'Secondary Schools Damaged (in Nos)', 'PWSS Damaged (in Nos)', 'P

In [25]:

# Function to extract unique dictionary keys
# Function to extract unique dictionary keys, excluding keys with "."
def extract_unique_keys(d, parent_key='', keys_set=None):
    if keys_set is None:
        keys_set = set()  # Initialize the set for unique keys

    if isinstance(d, dict):
        for k in d.keys():
            new_key = f"{parent_key}.{k}" if parent_key else k
            # Exclude keys that contain a period
            if '.' not in new_key:
                keys_set.add(new_key)  # Add key to the set
            extract_unique_keys(d[k], new_key, keys_set)
    elif isinstance(d, list):
        for item in d:
            extract_unique_keys(item, parent_key, keys_set)
    
    return keys_set


# Extract unique keys from the JSON structure
unique_keys = extract_unique_keys(data_file)

# Convert the set to a sorted list for easier readability
sorted_unique_keys = sorted(unique_keys)

# Print the extracted unique keys
for key in sorted_unique_keys:
    print(key)

affectedDistricts
affectedPopulation
affectedRevenueCircles
affectedVillages
campInmates
cwcDetails
hllDetails
houseDamagedDetails
infDamageDetails
livestocksDetails
nonCampInmates
otherDamageDetails
reliefCampsAndCenters
reliefDistributionDetails
remarks
rescueOperationDetails
wildlife


#### Indicators to extract:

#### important:
affectedPopulation, hllDetails, infDamageDetails, 

###### Not at RC level:
houseDamagedDetails, livestocksDetails

#### could be useful:
campInmates
nonCampInmates
otherDamageDetails
reliefCampsAndCenters
reliefDistributionDetails
rescueOperationDetails
wildlife

###### Not at RC Level:


#### Relief Inmates

In [15]:
data = open(r'D:\CivicDataLab_IDS-DRR\IDS-DRR_Github\IDS-DRR-Assam\Sources\FRIMS\data\DRIMS_api_output\2024_06.json')
data_file = json.load(data)
campinmates = data_file["campInmates"]
#df = df.sort_values('total', ascending=False)
campinmates


[{'total': 194,
  'totalMale': 55,
  'totalFemale': 90,
  'totalChildren': 45,
  'totalPregnant': 3,
  'totalDisabled': 1,
  'district': 'Bajali',
  'details': '(Bajali | 42), (Sarupeta | 152)'},
 {'total': 117,
  'totalMale': 29,
  'totalFemale': 43,
  'totalChildren': 39,
  'totalPregnant': 6,
  'totalDisabled': 0,
  'district': 'Baksa',
  'details': '(Barnagar RC part | 0), (Baska | 0), (Jalah | 117)'},
 {'total': 0,
  'totalMale': 0,
  'totalFemale': 0,
  'totalChildren': 0,
  'totalPregnant': 0,
  'totalDisabled': 0,
  'district': 'Barpeta',
  'details': '(Barnagar | 0), (Sarthebari | 0), (Barpeta | 0)'},
 {'total': 0,
  'totalMale': 0,
  'totalFemale': 0,
  'totalChildren': 0,
  'totalPregnant': 0,
  'totalDisabled': 0,
  'district': 'Biswanath',
  'details': '(Halem | 0), (Gohpur | 0)'},
 {'total': 0,
  'totalMale': 0,
  'totalFemale': 0,
  'totalChildren': 0,
  'totalPregnant': 0,
  'totalDisabled': 0,
  'district': 'Bongaigaon',
  'details': '(Manikpur | 0), (Dangtol | 0), (Bo

#### Other Damages

In [14]:
data = open(r'D:\CivicDataLab_IDS-DRR\IDS-DRR_Github\IDS-DRR-Assam\Sources\FRIMS\data\DRIMS_api_output\2024_06.json')
data_file = json.load(data)
other = data_file["otherDamageDetails"]
#df = df.sort_values('total', ascending=False)
other


[{'district': 'Bajali',
  'details': [{'block': 'Bajali',
    'damages': [{'damageName': 'Agri Bundh Damaged (in Nos)',
      'noOfDamage': 8,
      'details': [{'id': 46670,
        'name': 'Agri Bundh',
        'departmentName': 'P&RD',
        'villageName': 'Kalatoli Pathar',
        'location': 'At the left bank of Burhadiya river at Kalatoli pathar',
        'latitude': 26.39,
        'longitude': 91.23,
        'remarks': 'This agri bundh is breached at Kalatoli pathar, Length - apprx 10 mter and breadth 3mter.This report is received from Concerned Gaonpradhan of village Kalatoli Pathar on 19th june,2024',
        'createdAt': '2024-06-19T10:33:34.787Z',
        'updatedAt': '2024-06-19T10:33:34.787Z'},
       {'id': 46671,
        'name': 'Agri Bundh',
        'departmentName': 'P&RD',
        'villageName': 'Parakuchi Gaon',
        'location': 'At the right bank of Burhadiya river at Parahkuchi gaon',
        'latitude': 26.4,
        'longitude': 91.23,
        'remarks': 'T

### Houses damaged

In [13]:
data = open(r'D:\CivicDataLab_IDS-DRR\IDS-DRR_Github\IDS-DRR-Assam\Sources\FRIMS\data\DRIMS_api_output\2024_06.json')
data_file = json.load(data)
house = data_file["houseDamagedDetails"]
#df = df.sort_values('total', ascending=False)
house

{'damage': [{'district': 'Dhemaji',
   'noHdFullyKuccha': 0,
   'noHdFullyPukka': 0,
   'noHdPartiallyPukka': 0,
   'noHdPartiallyKuccha': 0,
   'totalFully': 0,
   'totalPartially': 0},
  {'district': 'Hailakandi',
   'noHdFullyKuccha': 0,
   'noHdFullyPukka': 0,
   'noHdPartiallyPukka': 0,
   'noHdPartiallyKuccha': 2592,
   'totalFully': 0,
   'totalPartially': 2592},
  {'district': 'Hojai',
   'noHdFullyKuccha': 82,
   'noHdFullyPukka': 2,
   'noHdPartiallyPukka': 15,
   'noHdPartiallyKuccha': 2365,
   'totalFully': 84,
   'totalPartially': 2380},
  {'district': 'Morigaon',
   'noHdFullyKuccha': 0,
   'noHdFullyPukka': 0,
   'noHdPartiallyPukka': 0,
   'noHdPartiallyKuccha': 0,
   'totalFully': 0,
   'totalPartially': 0},
  {'district': 'Karimganj',
   'noHdFullyKuccha': 0,
   'noHdFullyPukka': 0,
   'noHdPartiallyPukka': 0,
   'noHdPartiallyKuccha': 0,
   'totalFully': 0,
   'totalPartially': 0},
  {'district': 'Nagaon',
   'noHdFullyKuccha': 53,
   'noHdFullyPukka': 0,
   'noHdPar

#### Livestock

In [12]:
data = open(r'D:\CivicDataLab_IDS-DRR\IDS-DRR_Github\IDS-DRR-Assam\Sources\FRIMS\data\DRIMS_api_output\2022_06.json')
data_file = json.load(data)
livestock = data_file["livestocksDetails"]
#df = df.sort_values('total', ascending=False)
livestock



{'affected': [{'district': 'Bajali',
   'noLaBig': 87181,
   'noLaSmall': 37967,
   'noLaPoultry': 17600,
   'total': 142748},
  {'district': 'Baksa',
   'noLaBig': 20857,
   'noLaSmall': 15004,
   'noLaPoultry': 4300,
   'total': 40161},
  {'district': 'Barpeta',
   'noLaBig': 364729,
   'noLaSmall': 201811,
   'noLaPoultry': 520557,
   'total': 1087097},
  {'district': 'Biswanath',
   'noLaBig': 33911,
   'noLaSmall': 13244,
   'noLaPoultry': 0,
   'total': 47155},
  {'district': 'Bongaigaon',
   'noLaBig': 69868,
   'noLaSmall': 30923,
   'noLaPoultry': 119935,
   'total': 220726},
  {'district': 'Cachar',
   'noLaBig': 111513,
   'noLaSmall': 37569,
   'noLaPoultry': 49473,
   'total': 198555},
  {'district': 'Chirang',
   'noLaBig': 4360,
   'noLaSmall': 2588,
   'noLaPoultry': 2891,
   'total': 9839},
  {'district': 'Darrang',
   'noLaBig': 215726,
   'noLaSmall': 144631,
   'noLaPoultry': 108819,
   'total': 469176},
  {'district': 'Dhemaji',
   'noLaBig': 32967,
   'noLaSmall':

### Infra damages

In [4]:
data = open(r'D:\CivicDataLab_IDS-DRR\IDS-DRR_Github\IDS-DRR-Assam\Sources\FRIMS\data\DRIMS_api_output\2022_07.json')
data_file = json.load(data)
inf = data_file["infDamageDetails"]
#df = df.sort_values('total', ascending=False)
inf

{'embBreached': [{'district': 'Bajali',
   'total': 0,
   'details': [{'block': '(Sarupeta | 0)', 'details': []},
    {'block': '(Bajali | 0)', 'details': []}]},
  {'district': 'Baksa',
   'total': 0,
   'details': [{'block': '(Jalah | 0)', 'details': []}]},
  {'district': 'Barpeta',
   'total': 0,
   'details': [{'block': '(Barpeta | 0)', 'details': []},
    {'block': '(Baghbar | 0)', 'details': []},
    {'block': '(Sarthebari | 0)', 'details': []},
    {'block': '(Kalgachia | 0)', 'details': []},
    {'block': '(Chenga | 0)', 'details': []}]},
  {'district': 'Biswanath',
   'total': 0,
   'details': [{'block': '(Gohpur | 0)', 'details': []},
    {'block': '(Halem | 0)', 'details': []},
    {'block': '(Biswanath | 0)', 'details': []}]},
  {'district': 'Bongaigaon',
   'total': 1,
   'details': [{'block': '(Manikpur | 1)',
     'details': [{'id': 29320,
       'type': 'embBreached',
       'name': 'Embankment from Switch Gate to Abdul Barek house Ph-I',
       'departmentName': None,
 

In [5]:
data = inf

extracted_data = []

# Define the list of indicator types to iterate over
indicator_types = ["embBreached", "embAffected", "bridgeAffected", "roadAffected"]

# Iterate through each indicator type in the data
for indicator in indicator_types:
    if indicator in data:
        for entry in data[indicator]:
            district = entry['district']
            for detail in entry['details']:
                # Extract the block name and clean up the indicator value (remove parentheses)
                block = detail['block'].split('|')[0].strip('() ')
                indicator_value = detail['block'].split('|')[1].strip('() ')
                
                # Convert the cleaned value to an integer
                indicator_value = int(indicator_value)
                
                # Append a dictionary with the extracted data
                extracted_data.append({
                    'district': district,
                    'block': block,
                    'indicator': indicator,
                    'value': indicator_value
                })

# Convert the list to a DataFrame
df = pd.DataFrame(extracted_data)

# Pivot the table to get one row per block, and each indicator as a separate column
df_pivot = df.pivot_table(index=['district', 'block'], columns='indicator', values='value', fill_value=0).reset_index()

# Flatten the multi-level column index after pivot
df_pivot.columns.name = None  # Remove the index name from columns
df_pivot.columns = [col if isinstance(col, str) else col[1] for col in df_pivot.columns]

# Display the final DataFrame
print(df_pivot)

     district       block  bridgeAffected  embAffected  embBreached  \
0      Bajali      Bajali             1.0          8.0          0.0   
1      Bajali    Sarupeta             0.0          0.0          0.0   
2       Baksa       Jalah             0.0          0.0          0.0   
3     Barpeta     Baghbar             0.0          0.0          0.0   
4     Barpeta     Barpeta             8.0          0.0          0.0   
..        ...         ...             ...          ...          ...   
124  Udalguri   Harisinga             0.0          0.0          0.0   
125  Udalguri   Kalaigaon             0.0          0.0          0.0   
126  Udalguri  Khairabari             0.0          0.0          0.0   
127  Udalguri      Mazbat             0.0          0.0          0.0   
128  Udalguri    Udalguri             1.0          0.0          4.0   

     roadAffected  
0            65.0  
1             4.0  
2             0.0  
3            38.0  
4           197.0  
..            ...  
124    

### Human Lives Lost details

In [17]:
data = open(r'D:\CivicDataLab_IDS-DRR\IDS-DRR_Github\IDS-DRR-Assam\Sources\FRIMS\data\DRIMS_api_output\2022_06.json')
data_file = json.load(data)
hll = data_file["hllDetails"]
#df = df.sort_values('total', ascending=False)
hll

{'confirmed': [{'district': 'Nagaon',
   'floodDeath': 0,
   'generalDrowning': 0,
   'total': 6,
   'totalMale': 4,
   'totalFemale': 0,
   'totalChildrenMale': 1,
   'totalChildrenFemale': 1,
   'totalOthers': 0,
   'details': '(Nagaon | 1), (Raha | 3), (Kampur | 2), (Kaliabor | 0), (Samaguri | 0), (Rupahi | 0), (Dhing | 0)'},
  {'district': 'Cachar',
   'floodDeath': 0,
   'generalDrowning': 0,
   'total': 21,
   'totalMale': 16,
   'totalFemale': 0,
   'totalChildrenMale': 3,
   'totalChildrenFemale': 1,
   'totalOthers': 1,
   'details': '(Katigorah | 2), (Silchar | 11), (Lakhipur | 3), (Sonai | 4), (null | 0), (Udharbond | 1)'},
  {'district': 'Udalguri',
   'floodDeath': 0,
   'generalDrowning': 0,
   'total': 5,
   'totalMale': 2,
   'totalFemale': 0,
   'totalChildrenMale': 2,
   'totalChildrenFemale': 0,
   'totalOthers': 1,
   'details': '(Harisinga | 1), (Kalaigaon | 0), (Khairabari | 1), (Udalguri | 2), (Mazbat | 1)'},
  {'district': 'Karimganj',
   'floodDeath': 0,
   'ge

In [20]:
df = pd.DataFrame(hll)

# Function to extract the details column into a structured DataFrame
def extract_details(df_column, lives_lost_col):
    extracted_data = []
    
    for row in df_column:
        district = row['district']
        details = row['details']
        # Extract the revenue circle and lives lost information
        for match in details.split('), '):
            match = match.strip('()')
            revenue_circle, lives_lost = match.split(' | ')
            extracted_data.append({
                'district': district,
                'revenue_circle': revenue_circle.strip(),
                lives_lost_col: int(lives_lost)
            })
    
    return pd.DataFrame(extracted_data)

# Extract lives lost for both 'confirmed' and 'missing'
df_confirmed = extract_details(df['confirmed'], 'lives_lost_confirmed')
df_missing = extract_details(df['missing'], 'lives_lost_missing')

# Merge the two DataFrames on 'district' and 'revenue_circle'
df_final = pd.merge(df_confirmed, df_missing, on=['district', 'revenue_circle'], how='outer')

df_final

district    revenue_circle  lives_lost_confirmed  lives_lost_missing
0      Bajali            Bajali                     3                   0
1      Bajali          Sarupeta                     0                   0
2       Baksa         Baganpara                     0                   0
3       Baksa            Barama                     0                   0
4       Baksa  Barnagar RC part                     0                   0
..        ...               ...                   ...                 ...
143  Udalguri         Harisinga                     1                   0
144  Udalguri         Kalaigaon                     0                   0
145  Udalguri        Khairabari                     1                   0
146  Udalguri            Mazbat                     1                   0
147  Udalguri          Udalguri                     2                   0

[148 rows x 4 columns]

### Population + Crop Affected

In [8]:
data = open(r'D:\CivicDataLab_IDS-DRR\IDS-DRR_Github\IDS-DRR-Assam\Sources\FRIMS\data\DRIMS_api_output\2024_08.json')
data_file = json.load(data)
pop = pd.DataFrame(data_file["affectedPopulation"])
#df = df.sort_values('total', ascending=False)
pop

total  totalMale  totalFemale  totalChildren  totalCropArea  \
0       0          0            0              0           0.00   
1       0          0            0              0           0.00   
2       0          0            0              0           0.00   
3       0          0            0              0           0.00   
4   31290      12833         9876           8581        5410.00   
5       0          0            0              0           0.00   
6     223         99           89             35          20.00   
7    2596       1217         1140            239           6.00   
8       0          0            0              0           0.00   
9   18227       6806         6707           4714        2304.50   
10      0          0            0              0           0.00   
11   1080        364          356            360          16.50   
12  15342       6576         5581           3185        2010.40   
13    947        403          377            167         105.00   
14      0          0            0              0          20.00   
15      0          0            0              0           0.00   
16   2541        989         1044            508         220.00   
17  15305       5642         5208           4455        2119.00   
18      0          0            0              0           0.00   
19   2084       1095          726            263        1803.00   
20  48031      19290        15929          12812        2047.50   
21      0          0            0              0           0.00   
22      0          0            0              0          11.43   
23    161         95           59              7          10.03   

         district districtCode  \
0          Bajali           34   
1         Barpeta           02   
2      Bongaigaon           08   
3          Cachar           03   
4       Charaideo           07   
5         Chirang           09   
6         Darrang           04   
7         Dhemaji           05   
8          Dhubri           10   
9       Dibrugarh           11   
10     Dima-Hasao           12   
11       Goalpara           13   
12       Golaghat           14   
13     Hailakandi           15   
14         Jorhat           17   
15     Kamrup (M)           18   
16  Karbi Anglong           20   
17      Karimganj           22   
18      Lakhimpur           24   
19         Nagaon           27   
20      Sivasagar           29   
21       Sonitpur           30   
22       Tamulpur           35   
23       Udalguri           33   

                                              details  
0   (Sarupeta | Population Affected: 0 | Crop Area...  
1   (Barpeta | Population Affected: 0 | Crop Area: 0)  
2   (Bongaigaon | Population Affected: 0 | Crop Ar...  
3   (Silchar | Population Affected: 0 | Crop Area:...  
4   (Sapekhati | Population Affected: 4839 | Crop ...  
5     (Sidli | Population Affected: 0 | Crop Area: 0)  
6   (Mangaldoi | Population Affected: 223 | Crop A...  
7   (Jonai | Population Affected: 139 | Crop Area:...  
8   (South Salmara Part | Population Affected: 0 |...  
9   (Tengakhat | Population Affected: 135 | Crop A...  
10  (Haflong | Population Affected: 0 | Crop Area: 0)  
11  (Matia | Population Affected: 1080 | Crop Area...  
12  (Golaghat | Population Affected: 2477 | Crop A...  
13  (Hailakandi | Population Affected: 621 | Crop ...  
14  (Jorhat West | Population Affected: 0 | Crop A...  
15  (Sonapur | Population Affected: 0 | Crop Area: 0)  
16  (Phuloni | Population Affected: 2541 | Crop Ar...  
17  (Karimganj | Population Affected: 0 | Crop Are...  
18  (Subansiri | Population Affected: 0 | Crop Are...  
19  (Kaliabor | Population Affected: 1954 | Crop A...  
20  (Nazira | Population Affected: 108 | Crop Area...  
21  (Dhekiajuli | Population Affected: 0 | Crop Ar...  
22  (Goreswar | Population Affected: 0 | Crop Area...  
23  (Udalguri | Population Affected: 0 | Crop Area...

In [9]:
data_list = []
for index, row in pop.iterrows():
    district = row['district']  # Capture the district for the current row
    details = row['details']  # Capture the details for the current row
    
    # Find matches for the current details string
    match = re.findall(r'\(\s*(.*?)\s*\)', details)
    
    for m in match:
        try:
            # Split the extracted string by ' | ' to get the revenue circle, population affected, and crop area
            revenue_circle, population_affected, crop_area = m.split(' | ')
            population_affected = int(re.search(r'\d+', population_affected).group())
            crop_area = float(re.search(r'\d+(\.\d+)?', crop_area).group())
            
            # Append the results as a dictionary to the list, including the correct district
            data_list.append({
                "district": district,  # Add the correct district value here
                "Revenue Circle": revenue_circle.strip(),
                "Population Affected": population_affected,
                "Crop Area": crop_area
            })
        except Exception as e:
            print("Error processing match:", m, e)

# Create a DataFrame from the collected data
df_extracted = pd.DataFrame(data_list)

df_extracted

district Revenue Circle  Population Affected  Crop Area
0       Bajali       Sarupeta                    0       0.00
1      Barpeta        Barpeta                    0       0.00
2   Bongaigaon     Bongaigaon                    0       0.00
3       Cachar        Silchar                    0       0.00
4       Cachar      Udharbond                    0       0.00
..         ...            ...                  ...        ...
65    Tamulpur       Goreswar                    0      11.43
66    Udalguri       Udalguri                    0       0.00
67    Udalguri      Kalaigaon                    0       0.00
68    Udalguri      Harisinga                    0      10.03
69    Udalguri         Mazbat                  161       0.00

[70 rows x 4 columns]

#### Consolidated dataframe

In [31]:
# Define the data folder containing the JSON files
data_folder = r'D:\CivicDataLab_IDS-DRR\IDS-DRR_Github\IDS-DRR-Assam\Sources\FRIMS\data\DRIMS_api_output'

# Initialize a list to hold all JSON file paths
json_files = []
years = ['2022', '2023', '2024']
months = ['06', '07', '08', '09']
indicators = [
    'affectedPopulation',
    #'affectedRevenueCircles',
    #'affectedVillages',
    'campInmates',
    #'cwcDetails',
    'hllDetails',
    'houseDamagedDetails',
    'infDamageDetails',
    'livestocksDetails',
    'nonCampInmates',
    'otherDamageDetails',
    'reliefCampsAndCenters',
    'reliefDistributionDetails',
    'wildlife'
]

# Loop through years and months to gather JSON files
for year in years:
    for month in months:
        # Construct the expected file path pattern for JSON files
        json_file_pattern = os.path.join(data_folder, f"{year}_{month}*.json")
        files = glob.glob(json_file_pattern)
        json_files.extend(files)  # Add the files to the json_files list
json_files

# Initialize the dataframe that will hold merged data
district_ld = pd.DataFrame()

# Process each JSON file and merge the data
for json_file in json_files:
    try:
        # Read the JSON file
        with open(json_file, 'r') as data:
            data_file = json.load(data)
        
            # Extract data for each indicator and append to the main dataframe
            for indicator in indicators:
                if indicator in data_file:
                    ind = data_file[indicator]

                    df = pd.DataFrame(ind)
                    
                    # Extract year and month from the filename for the timeperiod
                    year_month = os.path.basename(json_file).split('_')[:2]  # e.g., ['2022', '06']
                    timeperiod = f"{year_month[0]}_{year_month[1]}"

                    # Add timeperiod to the dataframe
                    df['timeperiod'] = timeperiod
                    
                    # Merge the data into the final dataframe based on 'district' and 'timeperiod'
                    if district_ld.empty:
                        district_ld = df
                    else:
                        # Merge on 'district' and 'timeperiod', using '_new' suffix for any duplicate columns
                        district_ld = pd.merge(district_ld, df, on=['district', 'timeperiod'], how='outer', suffixes=('', '_new'))

                        # Fill in empty values in the original columns with values from the new columns
                        for col in df.columns:
                            if col in district_ld.columns:
                                if '_new' in col:
                                    original_col = col.replace('_new', '')
                                    # Update the original column with values from the new column
                                    district_ld[original_col] = district_ld[original_col].fillna(district_ld[col])
                                    # Drop the new column
                                    district_ld.drop(columns=[col], inplace=True)

    except Exception as e:
        print(f"Error processing file {json_file}: {e}")


Error processing file D:\CivicDataLab_IDS-DRR\IDS-DRR_Github\IDS-DRR-Assam\Sources\FRIMS\data\DRIMS_api_output\2022_06.json: 'district'
Error processing file D:\CivicDataLab_IDS-DRR\IDS-DRR_Github\IDS-DRR-Assam\Sources\FRIMS\data\DRIMS_api_output\2022_07.json: 'district'
Error processing file D:\CivicDataLab_IDS-DRR\IDS-DRR_Github\IDS-DRR-Assam\Sources\FRIMS\data\DRIMS_api_output\2022_08.json: 'district'
Error processing file D:\CivicDataLab_IDS-DRR\IDS-DRR_Github\IDS-DRR-Assam\Sources\FRIMS\data\DRIMS_api_output\2022_09.json: 'district'
Error processing file D:\CivicDataLab_IDS-DRR\IDS-DRR_Github\IDS-DRR-Assam\Sources\FRIMS\data\DRIMS_api_output\2023_06.json: 'district'
Error processing file D:\CivicDataLab_IDS-DRR\IDS-DRR_Github\IDS-DRR-Assam\Sources\FRIMS\data\DRIMS_api_output\2023_07.json: 'district'
Error processing file D:\CivicDataLab_IDS-DRR\IDS-DRR_Github\IDS-DRR-Assam\Sources\FRIMS\data\DRIMS_api_output\2023_08.json: 'district'
Error processing file D:\CivicDataLab_IDS-DRR\ID